In [1]:
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.feature_selection import chi2
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.naive_bayes import MultinomialNB
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.naive_bayes import MultinomialNB
from sklearn.svm import LinearSVC
import seaborn as sns
from sklearn.model_selection import cross_val_score
from sklearn.metrics import confusion_matrix
from sklearn import metrics
from sklearn.pipeline import Pipeline
from sklearn.linear_model import SGDClassifier
from sklearn.metrics import accuracy_score, confusion_matrix
from gensim.models import Word2Vec
import gzip
import gensim 
import logging
from itertools import islice
import multiprocessing
import nltk
from gensim.models import Word2Vec
import re
from nltk.corpus import stopwords
from bs4 import BeautifulSoup
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
from tqdm import tqdm
tqdm.pandas(desc="progress-bar")
from gensim.models import Doc2Vec
from sklearn import utils
from gensim.models.doc2vec import TaggedDocument
from tensorflow import keras
from keras.models import Sequential
from keras.layers import Dense, Activation, Dropout
from keras.preprocessing import text, sequence
from keras import utils
from sklearn.preprocessing import LabelBinarizer, LabelEncoder
from wordcloud import WordCloud, STOPWORDS, ImageColorGenerator
import Error
from matplotlib import reload
reload(Error)

C:\Program Files\Anaconda3\lib\site-packages\sklearn\ensemble\weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d
C:\Program Files\Anaconda3\lib\site-packages\gensim\utils.py:1212: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
C:\Program Files\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


<module 'Error' from 'U:\\JIRA\\Code\\Error.py'>

In [2]:
def replace_strings(data,name):
    for i in range(len(data)):
        if(data[name].iloc[i].find(',')!=-1):
            data[name].iloc[i]=data[name].iloc[i].split(",")[-1]
    return data

def word_averaging(wv, words):
    all_words, mean = set(), []
    
    for word in words:
        if isinstance(word, np.ndarray):
            mean.append(word)
        elif word in wv.vocab:
            mean.append(wv.vectors[wv.vocab[word].index])
            all_words.add(wv.vocab[word].index)

    if not mean:
        logging.warning("cannot compute similarity with no input %s", words)
        # FIXME: remove these examples in pre-processing
        return np.zeros(wv.vector_size,)

    mean = gensim.matutils.unitvec(np.array(mean).mean(axis=0)).astype(np.float32)
    return mean

def  word_averaging_list(wv, text_list):
    return np.vstack([word_averaging(wv, post) for post in text_list ])



def w2v_tokenize_text(text):
    tokens = []
    for sent in nltk.sent_tokenize(text, language='english'):
        for word in nltk.word_tokenize(sent, language='english'):
            if len(word) < 2:
                continue
            tokens.append(word)
    print(tokens)
    return tokens

REPLACE_BY_SPACE_RE = re.compile('[/(){}\[\]\|@,;]')
BAD_SYMBOLS_RE = re.compile('[^0-9a-z #+_]')
STOPWORDS = set(stopwords.words('english'))

def clean_text(text):
    """
        text: a string
        
        return: modified initial string
    """
    text = BeautifulSoup(text, "lxml").text # HTML decoding
    text = text.lower() # lowercase text
    text = REPLACE_BY_SPACE_RE.sub(' ', text) # replace REPLACE_BY_SPACE_RE symbols by space in text
    text = BAD_SYMBOLS_RE.sub('', text) # delete symbols which are in BAD_SYMBOLS_RE from text
    text = ' '.join(word for word in text.split() if word not in STOPWORDS) # delete stopwors from text
    return text

def label_sentences(corpus, label_type):
    """
    Gensim's Doc2Vec implementation requires each document/paragraph to have a label associated with it.
    We do this by using the TaggedDocument method. The format will be "TRAIN_i" or "TEST_i" where "i" is
    a dummy index of the post.
    """
    labeled = []
    for i, v in enumerate(corpus):
        label = label_type + '_' + str(i)
        labeled.append(TaggedDocument(v.split(), [label]))
    return labeled

def get_vectors(model, corpus_size, vectors_size, vectors_type):
    """
    Get vectors from trained doc2vec model
    :param doc2vec_model: Trained Doc2Vec model
    :param corpus_size: Size of the data
    :param vectors_size: Size of the embedding vectors
    :param vectors_type: Training or Testing vectors
    :return: list of vectors
    """
    vectors = np.zeros((corpus_size, vectors_size))
    for i in range(0, corpus_size):
        prefix = vectors_type + '_' + str(i)
        vectors[i] = model.docvecs[prefix]
    return vectors



In [3]:
data=pd.read_excel("U:/JIRA/JIRAExport/train_data.xls")
data=data.dropna()
data=replace_strings(data,'Component/s')
data.head()

C:\Program Files\Anaconda3\lib\site-packages\pandas\core\indexing.py:194: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)


Issue Key                                            Summary  Status  \
0  NCG3D-75861  CLONE - When a pohne without any music connect...  Closed   
1  NCG3D-75863                     Reset when system is kept idle  Closed   
2  NCG3D-75864                  Several resets during 35 km drive  Closed   
4  NCG3D-75867  After reaching the destination, the navi conti...  Closed   
5  NCG3D-75765  Map icons (compass, zoom scale and map menu) i...  Closed   

              Created        Component/s  \
0 2017-11-14 12:11:20    SW_INFOTAINMENT   
1 2017-11-14 12:38:12         SW_MANAPPS   
2 2017-11-14 12:48:53          SW_Resets   
4 2017-11-14 13:14:17      SW_NAVIGATION   
5 2017-11-14 06:58:13  SW_NAVIGATION_JPN   

                                         Description        Resolved Date  
0  h4. Test Environment :\n* HW Sample : P32R\n* ...  2018-01-24 10:25:31  
1  h4. Test Environment :\n* HW Sample : \n* Devi...  2017-11-15 07:12:04  
2  h4. Test Environment :\n* HW Sample : *dual li...  2017-11-14 14:02:45  
4  h4. Test Environment :\n* SW: 0734\n* HW Sampl...  2017-11-22 11:12:34  
5  h4. Test Environment :\n* HW Sample : Nissan P...  2017-12-07 12:31:42

In [4]:
X = data.Summary
y = data['Component/s']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state = 42)

In [5]:
sgd = Pipeline([('vect', CountVectorizer()),
                ('tfidf', TfidfTransformer()),
                ('clf', SGDClassifier(loss='hinge', penalty='l2',alpha=1e-3, random_state=42, max_iter=5, tol=None)),
               ])
sgd.fit(X_train, y_train)
y_pred = sgd.predict(X_test)
print('accuracy %s' % accuracy_score(y_pred, y_test))

accuracy 0.6568799564138265


In [6]:
data['Summary'] = data['Summary'].str.replace('[^a-zA-Z]',' ').str.lower()
stop_re = '\\b'+'\\b|\\b'.join(nltk.corpus.stopwords.words('english'))+'\\b'
data['Summary'] = data['Summary'].str.replace(stop_re, '')
data['Summary'] = data['Summary'].str.split()

In [7]:
phrases = gensim.models.phrases.Phrases(data['Summary'].tolist())
phraser = gensim.models.phrases.Phraser(phrases)
data_phrased = phraser[data['Summary'].tolist()]

2019-01-04 14:32:34,341 : INFO : collecting all words and their counts
2019-01-04 14:32:34,342 : INFO : PROGRESS: at sentence #0, processed 0 words and 0 word types
2019-01-04 14:32:34,505 : INFO : PROGRESS: at sentence #10000, processed 90401 words and 50835 word types
2019-01-04 14:32:34,652 : INFO : PROGRESS: at sentence #20000, processed 181031 words and 86038 word types
2019-01-04 14:32:34,834 : INFO : PROGRESS: at sentence #30000, processed 272976 words and 115986 word types
2019-01-04 14:32:34,999 : INFO : PROGRESS: at sentence #40000, processed 363178 words and 141899 word types
2019-01-04 14:32:35,176 : INFO : PROGRESS: at sentence #50000, processed 453975 words and 165855 word types
2019-01-04 14:32:35,335 : INFO : PROGRESS: at sentence #60000, processed 544767 words and 187807 word types
2019-01-04 14:32:35,517 : INFO : PROGRESS: at sentence #70000, processed 635646 words and 208315 word types
2019-01-04 14:32:35,683 : INFO : PROGRESS: at sentence #80000, processed 727740 wo

In [8]:
multiprocessing.cpu_count()

8

In [9]:
w2v = gensim.models.word2vec.Word2Vec(sentences=data_phrased,workers=32)

2019-01-04 14:32:37,719 : INFO : collecting all words and their counts
2019-01-04 14:32:37,720 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2019-01-04 14:32:38,024 : INFO : PROGRESS: at sentence #10000, processed 78516 words, keeping 7985 word types
2019-01-04 14:32:38,264 : INFO : PROGRESS: at sentence #20000, processed 157358 words, keeping 10894 word types
2019-01-04 14:32:38,538 : INFO : PROGRESS: at sentence #30000, processed 237212 words, keeping 12911 word types
2019-01-04 14:32:38,828 : INFO : PROGRESS: at sentence #40000, processed 315579 words, keeping 14385 word types
2019-01-04 14:32:39,135 : INFO : PROGRESS: at sentence #50000, processed 394462 words, keeping 15697 word types
2019-01-04 14:32:39,398 : INFO : PROGRESS: at sentence #60000, processed 473098 words, keeping 16898 word types
2019-01-04 14:32:39,658 : INFO : PROGRESS: at sentence #70000, processed 552097 words, keeping 18015 word types
2019-01-04 14:32:39,905 : INFO : PROGRESS: at se

2019-01-04 14:32:45,891 : INFO : worker thread finished; awaiting finish of 2 more threads
2019-01-04 14:32:45,893 : INFO : worker thread finished; awaiting finish of 1 more threads
2019-01-04 14:32:45,895 : INFO : worker thread finished; awaiting finish of 0 more threads
2019-01-04 14:32:45,898 : INFO : EPOCH - 2 : training on 653316 raw words (541530 effective words) took 3.1s, 177400 effective words/s
2019-01-04 14:32:46,945 : INFO : EPOCH 3 - PROGRESS: at 41.29% examples, 217463 words/s, in_qsize 0, out_qsize 0
2019-01-04 14:32:47,952 : INFO : EPOCH 3 - PROGRESS: at 78.31% examples, 207551 words/s, in_qsize 0, out_qsize 0
2019-01-04 14:32:48,466 : INFO : worker thread finished; awaiting finish of 31 more threads
2019-01-04 14:32:48,468 : INFO : worker thread finished; awaiting finish of 30 more threads
2019-01-04 14:32:48,469 : INFO : worker thread finished; awaiting finish of 29 more threads
2019-01-04 14:32:48,471 : INFO : worker thread finished; awaiting finish of 28 more thread

2019-01-04 14:32:53,692 : INFO : worker thread finished; awaiting finish of 20 more threads
2019-01-04 14:32:53,693 : INFO : worker thread finished; awaiting finish of 19 more threads
2019-01-04 14:32:53,693 : INFO : worker thread finished; awaiting finish of 18 more threads
2019-01-04 14:32:53,695 : INFO : worker thread finished; awaiting finish of 17 more threads
2019-01-04 14:32:53,696 : INFO : worker thread finished; awaiting finish of 16 more threads
2019-01-04 14:32:53,697 : INFO : worker thread finished; awaiting finish of 15 more threads
2019-01-04 14:32:53,698 : INFO : worker thread finished; awaiting finish of 14 more threads
2019-01-04 14:32:53,699 : INFO : worker thread finished; awaiting finish of 13 more threads
2019-01-04 14:32:53,700 : INFO : worker thread finished; awaiting finish of 12 more threads
2019-01-04 14:32:53,701 : INFO : worker thread finished; awaiting finish of 11 more threads
2019-01-04 14:32:53,702 : INFO : worker thread finished; awaiting finish of 10 m

In [10]:
w2v.save('w2v_v1')

2019-01-04 14:32:53,716 : INFO : saving Word2Vec object under w2v_v1, separately None
2019-01-04 14:32:53,717 : INFO : not storing attribute vectors_norm
2019-01-04 14:32:53,718 : INFO : not storing attribute cum_table
2019-01-04 14:32:53,891 : INFO : saved w2v_v1


In [11]:
model = Word2Vec(data['Summary'], size=100, window=5, min_count=3, workers=4)

2019-01-04 14:32:53,898 : INFO : collecting all words and their counts
2019-01-04 14:32:53,901 : INFO : PROGRESS: at sentence #0, processed 0 words, keeping 0 word types
2019-01-04 14:32:53,919 : INFO : PROGRESS: at sentence #10000, processed 90401 words, keeping 5933 word types
2019-01-04 14:32:53,938 : INFO : PROGRESS: at sentence #20000, processed 181031 words, keeping 8244 word types
2019-01-04 14:32:53,960 : INFO : PROGRESS: at sentence #30000, processed 272976 words, keeping 10005 word types
2019-01-04 14:32:53,979 : INFO : PROGRESS: at sentence #40000, processed 363178 words, keeping 11368 word types
2019-01-04 14:32:53,998 : INFO : PROGRESS: at sentence #50000, processed 453975 words, keeping 12601 word types
2019-01-04 14:32:54,017 : INFO : PROGRESS: at sentence #60000, processed 544767 words, keeping 13746 word types
2019-01-04 14:32:54,039 : INFO : PROGRESS: at sentence #70000, processed 635646 words, keeping 14826 word types
2019-01-04 14:32:54,060 : INFO : PROGRESS: at sen

In [12]:
vectors = model.wv

In [13]:
list(islice(w2v.wv.vocab, 0, 13))

['clone',
 'without',
 'music',
 'connect',
 'hu',
 'via',
 'bt',
 'popup',
 'header',
 'contain',
 'reset',
 'system',
 'kept']

In [14]:
nltk.sent_tokenize('I have a problem with my phone and i dont know what to do', language='english')

['I have a problem with my phone and i dont know what to do']

In [15]:
data=pd.read_excel("U:/JIRA/JIRAExport/train_data.xls")
data=data.dropna()
data=replace_strings(data,'Component/s')
data.head()

C:\Program Files\Anaconda3\lib\site-packages\pandas\core\indexing.py:194: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)


Issue Key                                            Summary  Status  \
0  NCG3D-75861  CLONE - When a pohne without any music connect...  Closed   
1  NCG3D-75863                     Reset when system is kept idle  Closed   
2  NCG3D-75864                  Several resets during 35 km drive  Closed   
4  NCG3D-75867  After reaching the destination, the navi conti...  Closed   
5  NCG3D-75765  Map icons (compass, zoom scale and map menu) i...  Closed   

              Created        Component/s  \
0 2017-11-14 12:11:20    SW_INFOTAINMENT   
1 2017-11-14 12:38:12         SW_MANAPPS   
2 2017-11-14 12:48:53          SW_Resets   
4 2017-11-14 13:14:17      SW_NAVIGATION   
5 2017-11-14 06:58:13  SW_NAVIGATION_JPN   

                                         Description        Resolved Date  
0  h4. Test Environment :\n* HW Sample : P32R\n* ...  2018-01-24 10:25:31  
1  h4. Test Environment :\n* HW Sample : \n* Devi...  2017-11-15 07:12:04  
2  h4. Test Environment :\n* HW Sample : *dual li...  2017-11-14 14:02:45  
4  h4. Test Environment :\n* SW: 0734\n* HW Sampl...  2017-11-22 11:12:34  
5  h4. Test Environment :\n* HW Sample : Nissan P...  2017-12-07 12:31:42

In [16]:
data['Summary'] = data['Summary'].apply(clean_text)

In [17]:
train, test = train_test_split(data, test_size=0.2, random_state = 42)


In [18]:
train_tokenized=[]
for i in range(len(train)):
    train_tokenized.append(w2v_tokenize_text(train['Summary'].iloc[i]))

['aivibp375', 'route', 'map', 'readable']
['glitch', 'observed', 'bt', 'audio']
['input', 'text', 'fileds', 'intesection', 'screen', 'completely', 'unaccessible']
['swc', 'hk', 'work', 'carplay', 'sporadically']
['sudden', 'unexpected', 'voice', 'guide', 'turn', 'list', 'changed', 'maneuver']
['image', 'files', 'resolution', '7360x4912', 'displayed', 'target']
['power', 'test', 'displayed', 'music', 'info', 'different', 'playing', 'music']
['aivibp16272', 'audio', 'random', 'noise', 'generated', 'playing', 'usb', 'music', 'ending', 'carplay', 'siri', 'usb', 'audio', 'screen']
['auto', 'brightness', 'popup', 'flickers', 'toggling', 'day', 'night', 'mode']
['main', 'pcb7974', 'g01']
['scope', '20', 'row', 'poi', 'recognised', 'poi', 'category', 'list']
['poweroffon', 'exception', 'process', 'opt', 'bosch', 'navigation', 'bin', 'procnavout', 'sigsegv', '_znst8_rb_treeimst4pairikmmest10_select1stis2_est4lessimesais']
['source', 'text', 'always', 'displayed', 'english', 'tuner', 'screen', '

['freezeselect', 'fuel', 'station', 'sxm', 'fuel', 'station', 'screen', 'decide', 'destinationthen', 'destination', 'displayedafter', 'press', 'back', 'key', 'repeatedlyfinally', 'freeze', 'happens']
['sds', 'session', 'starting']
['scope21', 'renault', 'dab', 'portrait', 'received', 'station', 'logos', 'shown', 'presets']
['keyboard', 'type', 'keyboard']
['nissan_21_lead', 'screen', 'freezes', 'selecting', 'city', 'center', 'shortcut', 'home', 'menu']
['can', 'not', 'scroll', 'zoom', 'zoom']
['scope', '20', 'cdt', 'hcm', 'ecu', 'reads', 'ff', 'even', 'configuration', 'cangen3']
['shortcut', 'bugwhen', 'quick', 'dial', 'shortcut', 'pressed', 'sound', 'comes', 'transit', 'quick', 'dial', 'screen']
['sxm', 'movies', 'selection', 'list', 'search', 'theater', 'screen', 'transitioning', 'theater', 'list']
['sxm', 'weather', 'text', 'allignment', 'proper', 'second', 'list', 'item']
['hu', 'locked', 'reentering', 'programming', 'session']
['scope2', 'time', 'physical', 'disconnection', 'aap',

['sxm', 'audio', 'presets', 'channels', 'changed', 'steering', 'wheel', 'control', 'buttons']
['zone', 'tab', 'button', 'appear', 'black', 'lines']
['reset', 'nissan', 'reset', 'observed', 'addying', 'waypoint', 'fom', 'poi', 'near', 'exit']
['sk_back', 'hk_back', 'transit', 'previous', 'screen', 'sxm', 'sports', 'scores', 'screen']
['home', 'location', 'yet', 'added', 'select', 'shortcut', 'home', 'result', 'transits', 'map', 'screen', 'add', 'home', 'location', 'confirmation', 'popup', 'displayed']
['aivibp19498', 'audio', 'scroll', 'bar', 'grayed', 'available', 'even', 'vehicle', 'speed', 'greater', 'edit', 'favorite', 'artist', 'screen']
['scope1', 'waiting', 'animation', 'displayed', 'long', 'time']
['aivibp9564', 'carplay', 'issue1', 'carplay', 'confirmation', 'disappears', 'disconnect', 'usb', 'upper', 'display', 'carplay', 'issue2', 'iphone', 'recognize', 'repeating', 'connection', 'disconnection', 'usb', 'iphone', 'upper', 'display']
['able', 'enter', 'inside', 'street', 'view

['change', 'navi', 'guidance', 'volume', 'possible', 'hmi', 'menu', 'volume', 'beeps', 'guidance', 'volume']
['aivibp9020', 'navigation', 'sk_others', 'top', 'sk', 'others', 'map', 'view', 'top', 'screen']
['systemd', 'founds', 'ordering', 'cycles', 'startup']
['seting', 'destination', 'place', 'around', 'freeway', 'exit', 'info', 'icon', 'around', 'freeway', 'exit', 'displayed', 'destination', 'list']
['apple', 'carplay', 'help', 'screen', 'content', 'fitting', 'inside', 'screen']
['map', 'carsor', 'disappeared', '3dsplit', 'map']
['phone', 'connected', 'popup', 'displayed', 'top', 'homemenu', 'main']
['back', 'transition', 'route', 'overview', 'screen', 'working']
['aivibp16226', 'phone', 'sms', 'call', 'screen', 'disappeared', 'selecting', 'sk_answer', 'incoming', 'call', 'screen', 'upper', 'display']
['aivibp187', 'impossible', 'select', 'city', 'center', 'find', 'address']
['scope21', 'cdt', 'ecu', 'lock', 'dtc', '0x934262', 'set', 'alliance', 'antitheft', 'configuration']
['state

['aivibp10127', 'navigation', 'information', 'street', 'name', 'displaying', 'nav_dest_map__0202_u', 'screen']
['state', 'change', 'failed', 'cca_c_u16_app_fc_mcan_meter', 'normal']
['sds', 'screen', 'still', 'displayed', 'even', 'sds', 'aborted']
['aivibp3782', 'settings', 'guest', 'profile', 'reset', 'go', 'sleep', 'wake', 'cycle']
['degrade', 'install', 'map', 'data', 'via', 'wifi']
['power', 'test', 'reboot', 'occurs']
['contents', 'service', 'test', 'mode', 'different', 'specifications']
['connected', 'phone', 'name', 'displayed', 'phone', 'menu', 'screen']
['aivibp4752', 'can', 'not', 'displayed', 'guidance', 'suspend', 'resume', 'button']
['nissannar', 'address', 'book', 'icons', 'shown', 'map']
['usb', 'ipod', 'track', 'number', 'number']
['zone', 'destination', 'text', 'displayed', 'poi']
['display', 'song', 'information', 'artist', 'song', 'name', 'album', 'changed', 'change', 'music', 'phone']
['launch', 'bar', 'visible', 'carplay', 'screen']
['aivibp5636', 'buttons', 'like'

...

['aivibp17807', 'fota', 'step', 'adas', 'hw', 'local', 'inventory', 'fails', 'unexpected', 'messages', 'ivi', 'cgw']
['bose', 'amp', 'jc', 'version', 'info', 'diagnosis', 'messages', 'send', 'amp', 'acc']
['jdp', 'issue', 'attempting', 'pinch', 'zoom', 'map', 'tends', 'change', 'perspective', 'map', 'views', '2d', 'birds', 'eye', 'view']
['pd', 'status', 'usb', 'port', 'always', 'ok', 'instead', 'implemented', 'port', 'switch']
['aivibp8249', 'smartphone', 'black', 'screen', 'appeared', 'lower', 'screen', 'system', 'wiress', 'carplay', 'music', 'playing']
['aivibp3277', 'hmi', 'weather', 'gadget', 'available', 'home', 'menu']
['unable', 'enter', 'nav__clickonmap_mapbrowser', 'view', 'map', 'view', 'zoom', 'working']
['sxm', 'audio', 'navigated', 'save', 'faovrite', 'sports', 'team', 'screen', 'sxm', 'main', 'screen', 'press', 'back', 'sk', 'hk', 'save', 'favorite', 'sports', 'team', 'screen', 'screen', 'navigates', 'sxm', 'menu', 'screen']
['rvc', 'gradation', 'characteristics']
['niss

['scope', '21', '_adas', 'behaviour', 'lane', 'assist', 'settings', 'screen', 'consistent']
['ch0', 'shown', 'hu', 'meter', 'shows', 'sxm', 'instead']
['lsim', 'assert', 'procmeter', 'application', 'set', 'normal']
['prc', 'item', 'numbers', 'displayed', 'settings', 'add', 'favorites']
['page', 'swipe', 'working', 'homemenu', 'main', 'bottom', 'empty', 'area']
['nissannar', 'ok', 'button', 'enabled', 'without', 'selecting', 'ambiguity', 'area', 'back', 'transition']
['source', 'change', 'every', 'swc', 'mode', 'button', 'press', 'rapid', 'pressing']
['aivibp6887', 'hmi', 'label', 'dislay', 'tpw_tirechekreminder']
['aivibp4675', 'vr', 'say', 'show', 'remove', 'poi', 'icons', 'parking', 'icon', 'setting', 'reflected', 'vr']
['constant', 'map', 'screen', 'flicker', 'turn', 'list', 'mode', 'active', 'displayed']
['aivibp11585', 'display', 'text', 'displayed', 'disclimer', 'screen', 'cold', 'start', 'screen']
['voice', 'prompt', 'echo', 'heard', 'voice', 'clarity', 'affected', 'voice', 'pre

['aivibp9392', 'issue1', 'system', 'display', 'list', 'soon', 'notification', 'press', 'vr', 'option', 'manual', 'operation', 'issue2', 'system', 'cancels', 'vr', 'moves', 'another', 'city', 'tab', 'cancels', 'vr', 'anyway', 'press', 'vr', 'option', 'repeatedly']
['one', 'signal', 'quality', 'value', 'displayed', 'although', 'two', 'phones', 'connected']
['cyclic', 'adrresets', 'tun_drvadrifvresetadr']
['sds_21_nissan_lead', 'sds', 'start', 'nederlands', 'selected', 'language', 'list']
['country', 'button', 'displayed', 'search', 'poi', 'address', 'screen']
['aivibp7369', 'bluetooth', 'switching', 'hf', 'bta', 'device', 'name', 'press', 'bta', 'connected', 'hf', 'connected']
['fixed', 'text', 'custom', 'text', 'text', 'message', 'settings', 'allignment', 'proper']
['selecting', 'sk', 'hk', 'back', 'wifi', 'information', 'screen', 'scroll', 'bar', 'wifi', 'connection', 'manager', 'screen', 'shifts', 'left', 'right']
['clone', 'aap_drivetest', 'audio', 'widget', 'homescreen', 'updated', 

['scope', '21', 'renault', 'balance', 'fader', 'list', 'bounce', 'back']
['aivibp9015', 'navigation', 'screen', 'change', 'press', 'sk_full', 'map']
['status', 'fm', 'head', 'unit', 'updating', 'even', 'fm', 'antenna', 'connected']
['request', 'language', 'dont', 'change', 'language', 'auto']
['played', 'audio', 'objects', 'mtp', 'device', 'limited', 'maximum', 'size', '10', 'mbyte']
['global', 'screen', 'help', 'back', 'commands', 'working', 'touch']
['scope', '21', 'nissan', 'action', 'selection', 'sk_map', 'update', 'system', 'information', 'screen']
['audio', 'general', 'rotate', 'vol', 'knob', 'quickly', 'feel', 'slow', 'volume', 'adjusted']
['aivibp270', 'sometimes', 'impossible', 'launch', 'guidance']
['aivibp4068', 'dcmack', 'logged', 'upload', 'manager']
['scope21', 'clone', 'earlysdsprompt', 'played', 'mexican', 'spanish', 'canadian', 'french', 'languages', 'row']
['focus', 'moved', 'phone', 'menu', 'icon', 'sds', 'root', 'screen']
['scope', '21', 'renault', 'audio', 'goes', 

['clone', 'navigation', 'speedlock', '17o', 'behavior', 'expected', 'screen', 'settings__nav_main_0001']
['continuous', 'connection', 'disconnection', 'aap', 'device', 'aap', 'doesnt', 'launch', 'displayed', 'error', 'popup']
['delay', 'connecting', 'network', 'connecting', 'bt', 'device']
['dacia', 'vehicle', 'multisense', 'map', 'seen', 'enter', 'screen']
['navi', 'roundaboutexit', 'state', 'end', 'sent', 'meter']
['outgoing', 'call', 'end', 'call', 'continuously', 'call', 'history', 'system', 'outgoing', 'call', 'call', 'history']
['aivibp3508', 'route', 'screen', 'text', 'cut']
['text', 'overlapped', 'traffic', 'ahead', 'popup']
['flick', 'operation', 'phonebook', 'screen', 'screen', 'transition', 'good', 'sometimes', 'blank', 'screen', 'displayed']
['b1sample', 'pcb', '9948', 'g01', 'overwind', 'screws', 'caused', 'cracked', 'screwing', 'pockets', 'front', 'plate']
['cancel', 'rg', 'works']
['turn', 'list', 'turn', 'list']
['dacia', 'landscape', 'header', 'coverflow', 'items']
['p

In [19]:
test_tokenized=[]
for i in range(len(test)):
    test_tokenized.append(w2v_tokenize_text(test['Summary'].iloc[i]))

['aivibp11297', 'ddi', 'phone', 'settings', 'smartphone', 'help', 'alignment', 'issue', 'page', 'navigation', 'arrows']
['dvd', 'subtitle', 'language', 'always', 'coming']
['aivibp8949', 'navigation', 'poi', 'icon', 'customized', 'category', 'dummy', 'image', 'simulator', 'press', 'sk_poi', 'destination', 'screen', 'page1', 'screen']
['personalisation', 'user', 'deletion', 'proper']
['aivibp19449', 'priority', 'matrix', 'volume', 'toast', 'popup', 'placed', 'overlay', 'wcbs', 'metal', 'piece', 'popup']
['gud_adj', 'temporary', 'swithcing', 'anticipatory', 'line', 'working', 'adjustements', 'screen']
['traffic', 'event', 'info', 'map', 'traffic', 'info', 'list']
['scope2', 'zxza20', 'screens', 'implemented', 'strictly', 'following', 'instruction', 'zxz']
['phone', 'bt', 'connection', 'stable']
['pivi', 'japan', 'information', 'screen', 'vehicle', 'information', 'showing']
['phonebook', 'loading', 'phone', 'connected', 'bt']
['phone', 'screens', 'accessible', 'receiving', 'incoming', 'ca

['exception', 'opt', 'bosch', 'base', 'bin', 'apphmi_telematics_outout', 'sigsegv']
['tunersxm', 'source', 'retained', 'properly', 'acc', 'offon']
['clone', 'new', 'route', 'found', 'popup', 'contains', 'overlapping', 'text']
['map', 'screen', 'displayed', 'instead', 'avm', 'rvc', 'camera', 'image']
['aivibp6973', 'gadgets', 'portrait', 'clock', 'gagdet', 'hmi', 'medium', 'size', 'per', 'expectations']
['nav_dest_freetext__0010_l', 'jpn', 'according', 'requirment', 'scroll', 'bar', 'display', 'page']
['phone', 'option', 'grayed', 'even', 'connection', 'establishment', 'bluetooth', 'vise', 'versa']
['setting', 'phone', 'notifications', 'driver', 'display', 'incoming', 'call', 'popup', 'phone', 'main', 'screen']
['scope1', 'permanent', 'carplay', 'blackscreen', 'avm', 'camera', 'view']
['va', 'screen', 'doesnot', 'stay']
['scope', '20', 'gesture', 'replay', 'happening', 'gesture', 'replay', 'start', 'set']
['sxm', 'traffic', 'traffic', 'event', 'description', 'displayed', 'empty']
['loca

['aivibp13104', 'audio', 'sk', 'repeat', 'active', 'power', 'test', 'startup', 'counter', '2times', 'mvi_3460ign', 'time', '00155', 'cd', 'screen']
['aivibp10619', 'phone', 'sms', 'hfp', 'icons', 'connections', 'grayed', 'bt', 'connect', 'successfully', 'popup', 'connections', 'screen']
['entering', 'wrong', 'password', 'pairing', 'legacy', 'device', 'pin', 'screen', 'flickers', 'second', 'time', 'pairing', 'failed', 'popup', 'displayed']
['nissannar', 'blue', 'route', 'remains', 'map', 'without', 'starting', 'route', 'guidance']
['scope21', 'renault', 'portrait', 'traffic', 'sign', 'displayed', 'driving', 'assistance', 'screen', 'even', 'though', 'osp', 'set', 'disabled', 'hmi', 'config', 'write']
['ipa_prc', 'message', 'ids', 'displayed', 'ipa', 'pattern']
['pivi', 'navigation', 'popup', 'location', 'received', 'smartphone', 'app', 'received', 'settings', 'destination', 'via', 'nissan', 'door', 'door', 'app']
['intersection', 'set', 'destination']
['area', 'setting', 'pop', 'remains'

['aivibp6533', 'mota', 'ivi', 'ic6', 'map', 'update', 'can', 'not', 'performed', 'due', 'security', 'policies']
['aivibp8357', 'degrade', 'display', 'country1of', 'unclear', 'sentence', 'displayed', 'input', 'enter', 'space', 'short', 'press', 'sk_free', 'text', 'search', 'free', 'text', 'screen']
['car', 'play', 'music', 'audio', 'heard', 'conneting', 'bt', 'call']
['siri', 'active', 'music', 'mute', 'pwr', 'button', 'press', 'audio', 'starts', 'play']
['traffic', 'messages', 'available', 'complete', 'shut']
['sonar', 'sonar', 'sk', 'accessible', 'parking', 'sonar', 'screen']
['entertainment', 'volume', 'muted', 'navi', 'volume', 'set', 'expected', 'limited', 'steps']
['lsim', 'bluetooth', 'box', 'longer', 'works']
['p32r', 'connecting', 'android', 'auto', 'adapted', 'smartphone', 'shortcut', 'evaluation', 'audio', 'screen', 'transiting', 'screen', 'can', 'not', 'made', 'even', 'depressing', 'hk', 'buttons', 'icons', 'launch', 'bar']
['view', 'backs', 'confirmation', 'adjustment', 'sc

['failure', 'retry', 'strategy', 'receiving', 'ecall_state', 'voicecallstop', 'audio', 'still', 'ecall', 'screen', 'switching', 'homemenu', 'screen']
['fm', 'mode', 'somtimes', 'audio', 'output', 'p32r', 'dv', 'lt', '03']
['setting', 'menu', 'list', 'can', 'not', 'behaive', 'desired']
['view', 'transfers', 'voice', 'recognition', 'tts', 'setting', 'instead', 'best', 'match', 'list', 'press', 'hk_back', 'popup', 'set', 'best', 'match', 'list', 'shown', 'phonebook', 'name', 'recognition']
['png', 'bmp', 'images', 'displayed', 'target']
['aivibp20036', 'restrictions', 'portrait', 'restrictions', 'failed', 'occur', 'clim', 'eco', 'setting', 'page', 'countries', 'like', 'mex', 'jpn']
['meter', 'cluster', 'switching', 'back', 'forth', 'next', 'turn', 'manuver', 'screen', 'audio', 'screen']
['scope2', 'bottom', 'screen', 'bar', 'icons', 'displayed', 'always', 'carplay', 'screen', 'use', 'swc_sourcechange']
['range', 'sxm', 'channel', 'numbers', 'accepted', 'sds']
['navi', 'without', 'entering

...

['system', 'restarted', 'system', 'shutdown', 'ongoing', 'call', 'time', 'updated']
['pivi', 'navigation', 'map', 'compass', 'button', 'working', 'intersection', 'screen']
['stm', 'order', 'serial', 'info', 'dispayed', 'stm', 'version']
['back', 'key', 'pressed', 'screen', 'changes', 'previous', 'two', 'screen']
['improve', 'score', 'accelerate', 'brake', 'slower', 'displayed', 'eco', 'drive', 'report', 'view']
['tcu', 'xcall', 'didnt', 'start', 'ecall', 'end']
['2f900703xx', 'rear_camera_configuration_control', 'returned', 'nrc', '0x31']
['reset', 'observed', 'pressing', 'next_hk', 'fm', 'menu', 'menu', 'exception', 'process', 'pid417', 'thtunerhmi']
['pivi', 'navigation', 'route', 'add', 'route', 'screen', 'flickers', 'upper', 'display', 'screen']
['aivibp3098', 'video', 'fastforward', 'x02', 'x05', 'x2', 'x4', 'x8', 'x16', 'x32', 'arent', 'functioning', 'correcty']
['language', 'characters', 'seen', 'pressing', 'aeb', 'button', 'edit', 'address', 'entry']
['scope', 'confirmation', '

['accepting', 'incoming', 'call', '2nd', 'hfp', 'via', 'handset', 'handsfree', 'call', 'active', '1st', 'hfp', 'handsfree', 'call', '1st', 'hfp', 'ends']
['clone', 'changing', 'size', 'wording', 'size', 'poi', 'icon', 'also', 'interlocking', 'changed']
['right', 'encoder', 'rotation', 'behaving', 'properly', 'quick', 'search', 'active', 'phonebook', 'contact']
['leading', 'zeros', 'eta', 'numbers']
['pivi', 'full', 'system', 'hang']
['sxm', 'sports', 'time', 'going', 'screen', 'scheduled', 'timestamp', 'future', 'game', 'screen']
['aivibp3292', 'settings', 'lock', 'button', 'displayed', 'coverflow', 'picture']
['clone', 'zoom', 'scale', 'buttons', 'consistant']
['exception', 'opt', 'bosch', 'base', 'bin', 'app_fcota_outout', 'sigabrt']
['unable', 'play', 'track', 'media', 'source', 'cd', 'usb']
['portrait', 'zone1', 'background', 'map']
['hmi', 'directly', 'jumps', 'beginning', 'list', 'pressing', 'back']
['footer', 'changes', 'blank', 'moving', 'sxm', 'menu', 'screen', 'pressing', 'me

['aivibp13125', 'photo', 'slideshow', 'started', 'photoplayer', 'screen']
['traffic', 'icons', 'map', 'screen', 'disappeared', 'even', 'internet', 'disconnected', 'hours']
['calling', 'screen', 'frozen', 'display']
['press', 'hk', 'audio', 'key', 'long', 'press', 'behavior', 'short', 'press', 'fm0405_switch', 'matrix_ver16']
['clone', 'phone', 'icon', 'appears', 'map', 'launch', 'bar', 'instead', 'aap', 'complete']
['sett', 'nissan', 'logo', 'always', 'observed', 'blank', 'screen', 'hmi', 'korean', 'region', 'change']
['aivi', 'scope2', 'v850', 'trc', 'file', 'uptodate', 'unspecified', 'v850', 'trace', 'modid', 'flexray_nm__']
['aivibp328', 'find', 'address', 'keyboards', 'reaction', 'low', 'impossible', 'set', 'house', 'number', 'addresses']
['possible', 'shift', 'preset', 'main', 'screen']
['sxm', 'weather', 'start', 'time', 'end', 'time', 'display', 'proper']
['macthes', 'city', 'shown', 'special', 'characters']
['previous', 'traffic', 'data', 'displayed', 'map', 'screen', 'selectin

['aivibp12576', 'audio', 'dtv', 'sound', 'countinues', 'play', 'even', 'walkman', 'connected', 'usb2', 'sk_usb2', 'short', 'pressed', 'lower', 'display']
['aivibp3161', 'press', 'ev', 'info', 'info', 'screen', 'changes', 'map', 'screen', 'freezesraguram', 'san', 'got', 'log', '1655', '20']
['bt', 'translation', 'phone', 'top', 'text', 'showing', 'japanese', 'even', 'though', 'system', 'language', 'set', 'english']
['aivibp10201', 'meter', 'hud', 'hud', 'button', 'clickble', 'hud', 'main', 'sw', 'status', 'short', 'press', 'sk_hud', 'hud']
['aivibp16552', 'system', 'reboot', 'occurs', 'mapupdate', 'finished', 'mapupdate', 'screen']
['aivibp393', 'guidance', 'screen', 'previous', 'destinations', 'still', 'displayed', 'map', 'even', 'manually', 'cancelled']
['lower', 'case', 'key', 'working', 'edit', 'address', 'book', 'entry']
['even', 'though', 'deleting', 'items', 'hutching', 'applied', 'button']
['scroll', 'direction', 'setting', 'secreen', 'display', 'setting', 'customers', 'select',

['tuning', 'action', 'psd', 'data', 'hold', 'time', 'leads', 'hd', 'radio', 'logo', 'white']
['time', 'lag', 'play', 'counter', 'ipod', 'play', 'counter', 'time', 'play', 'counter', 'one', 'second', 'behind', 'ipod', 'play', 'counter']
['aivibp7845', 'system', 'doesnt', 'highlight', 'current', 'station', 'fm', 'list']
['aivibp8098', 'display', 'selected', 'gadget', 'type', 'displayed', 'selecting', 'gadget', 'type', 'gadget', 'setting', 'screen', 'udm']
['reset', 'observed', 'photoviewer', 'file', 'selection']
['aivibp3360', 'hmi', 'system', 'getting', 'reboot', 'factory', 'reset', 'button', 'selected']
['aivibp2604', 'option', 'changing', 'date', 'format', 'text', 'number']
['navi', 'hmi', 'hang', 'giving', 'input', 'street', 'address']
['sub', 'pcb', '7216', 'g01']
['sxm', 'audio', 'deselect', 'city', 'traffic', 'weather', 'nowsettings', 'screen', 'press', 'twn', 'icon', 'sxm', 'main', 'screen', 'popup', 'select', 'city', 'seen']
['main', '0275', 'traffic', 'confirmation', 'window', 

In [20]:
X_train_word_average = word_averaging_list(w2v.wv,train_tokenized)
X_test_word_average = word_averaging_list(w2v.wv,test_tokenized)

2019-01-04 14:46:04,564 : WARNING : cannot compute similarity with no input ['z3', 'motion']
2019-01-04 14:46:04,564 : WARNING : cannot compute similarity with no input ['mainboard', '6598', 'g02']
2019-01-04 14:46:04,627 : WARNING : cannot compute similarity with no input ['mainboard', '7974', 'g01']
2019-01-04 14:46:04,627 : WARNING : cannot compute similarity with no input ['nav__freetextsearch_main']
2019-01-04 14:46:04,658 : WARNING : cannot compute similarity with no input ['avmcamera', 'beepsoundrespons']
2019-01-04 14:46:04,674 : WARNING : cannot compute similarity with no input ['mainboard', '6598', 'g03']
2019-01-04 14:46:04,689 : WARNING : cannot compute similarity with no input ['ehmi_app_error', 'systemstate', 'spm_system_on']
2019-01-04 14:46:04,705 : WARNING : cannot compute similarity with no input ['nav__route_editcreateroute']
2019-01-04 14:46:04,720 : WARNING : cannot compute similarity with no input ['nav__rc_routecalculationwithoutalternativeroute1']
2019-01-04 14:

2019-01-04 14:46:06,689 : WARNING : cannot compute similarity with no input ['aivibp17729', 'ecallprivateecall_abnormalcase_retry']
2019-01-04 14:46:06,736 : WARNING : cannot compute similarity with no input ['mainboard', '6598g02']
2019-01-04 14:46:06,752 : WARNING : cannot compute similarity with no input ['pm_cyclic_imx_reset_detected']
2019-01-04 14:46:06,767 : WARNING : cannot compute similarity with no input ['traffic_list']
2019-01-04 14:46:06,767 : WARNING : cannot compute similarity with no input ['fancontrol']
2019-01-04 14:46:06,830 : WARNING : cannot compute similarity with no input ['sw_n']
2019-01-04 14:46:06,986 : WARNING : cannot compute similarity with no input ['aivibp2676', 'summarytest']
2019-01-04 14:46:07,033 : WARNING : cannot compute similarity with no input ['nav__ps_petrolstationdetail']
2019-01-04 14:46:07,048 : WARNING : cannot compute similarity with no input ['aivibp14607', 'l42p', 'st21', '5th', '0x25', 'vdiag', 'f1a12591a', '6ct0b']
2019-01-04 14:46:07,0

In [21]:
logreg = LogisticRegression(n_jobs=7,penalty='l2', C=1e5)
logreg = logreg.fit(X_train_word_average, train['Component/s'])
y_pred = logreg.predict(X_test_word_average)
np.mean(y_pred==test['Component/s'])

C:\Program Files\Anaconda3\lib\site-packages\sklearn\linear_model\logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = 7.
  " = {}.".format(self.n_jobs))


0.595798777165688

In [22]:
Error.err.class_err(test['Component/s'],y_pred)

SW_FRAMEWORK_HMI 0.031746031746031744
SW_INFOTAINMENT 0.7145343777197564
SW_NAVIGATION_JPN 0.09
SW_PROFILE 0.5641025641025641
SW_Master_HMI 0.12771739130434784
SW_PARKASSIST 0.7508196721311475
SW_NAVIGATION 0.8656338918748024
SW_PHONE 0.7757125154894672
SW_SPEECH 0.6771507863089732
SW_DIAGNOSTIC 0.5546038543897216
SW_SMARTPHONE 0.7358657243816255
SW_TUNER_SXM 0.8159392789373814
SW_SYSTEM 0.37169811320754714
SW_TUNER_DAB 0.5116279069767442
SW_TUNER_AMFM 0.6353166986564299
SW_TRANSLATIONS 0.12258064516129032
SW_Resets 0.4580152671755725
SW_DRIVEASSIST 0.4594594594594595
SW_HOME_MENU 0.5
TEST_FEP 0.05555555555555555
SW_TUNER_HD 0.5
SW_AUDIO 0.34124629080118696
SW_TELEMATIC 0.3556085918854415
SW_SWUPDATE 0.64
SW_DEBUG_TRACE 0.11538461538461539
SW_ADASIS 0.0
SW_TUNER_TV 0.4270833333333333
SW_WIFI 0.6480446927374302
SW_METER 0.5313807531380753
SW_ARCHITECTURE 0.125
SW_DATA 0.03278688524590164
SW_OTAS 0.27848101265822783
TEST_ZTEST 0.2777777777777778
SW_WIDGETS 0.0
Mechanic 0.6785714285714286

In [23]:
logreg = LogisticRegression(n_jobs=7,penalty='l2', C=1e5,solver='newton-cg')
logreg = logreg.fit(X_train_word_average, train['Component/s'])
y_pred = logreg.predict(X_test_word_average)
np.mean(y_pred==test['Component/s'])

0.5956777044615291

In [24]:
Error.err.class_err(test['Component/s'],y_pred)

SW_FRAMEWORK_HMI 0.031746031746031744
SW_INFOTAINMENT 0.7145343777197564
SW_NAVIGATION_JPN 0.09
SW_PROFILE 0.5641025641025641
SW_Master_HMI 0.125
SW_PARKASSIST 0.7491803278688525
SW_NAVIGATION 0.8653177363262725
SW_PHONE 0.7757125154894672
SW_SPEECH 0.6771507863089732
SW_DIAGNOSTIC 0.556745182012848
SW_SMARTPHONE 0.7340989399293286
SW_TUNER_SXM 0.8159392789373814
SW_SYSTEM 0.37169811320754714
SW_TUNER_DAB 0.5116279069767442
SW_TUNER_AMFM 0.6372360844529751
SW_TRANSLATIONS 0.11612903225806452
SW_Resets 0.4580152671755725
SW_DRIVEASSIST 0.4594594594594595
SW_HOME_MENU 0.5
TEST_FEP 0.05555555555555555
SW_TUNER_HD 0.5
SW_AUDIO 0.34124629080118696
SW_TELEMATIC 0.35799522673031026
SW_SWUPDATE 0.64
SW_DEBUG_TRACE 0.11538461538461539
SW_ADASIS 0.0
SW_TUNER_TV 0.4270833333333333
SW_WIFI 0.6480446927374302
SW_METER 0.5355648535564853
SW_ARCHITECTURE 0.125
SW_DATA 0.03278688524590164
SW_OTAS 0.27848101265822783
TEST_ZTEST 0.2777777777777778
SW_WIDGETS 0.0
Mechanic 0.6785714285714286
SW_GRAPHICS 0

In [ ]:
logreg = LogisticRegression(n_jobs=7,penalty='l2', C=1e6,solver='newton-cg')
logreg = logreg.fit(X_train_word_average, train['Component/s'])
y_pred = logreg.predict(X_test_word_average)
np.mean(y_pred==test['Component/s'])

In [ ]:
Error.err.class_err(test['Component/s'],y_pred)

In [ ]:
logreg = LogisticRegression(n_jobs=7,penalty='l2', C=1e4,solver='newton-cg')
logreg = logreg.fit(X_train_word_average, train['Component/s'])
y_pred = logreg.predict(X_test_word_average)
np.mean(y_pred==test['Component/s'])

In [ ]:
Error.err.class_err(test['Component/s'],y_pred)

In [ ]:
print('accuracy %s' % (accuracy_score(y_pred, test['Component/s'])))

In [ ]:
logreg = LogisticRegression(n_jobs=7,penalty='l2', C=1e4,solver='lbfgs')
logreg = logreg.fit(X_train_word_average, train['Component/s'])
y_pred = logreg.predict(X_test_word_average)
np.mean(y_pred==test['Component/s'])

In [ ]:
Error.err.class_err(test['Component/s'],y_pred)

In [ ]:
X_train, X_test, y_train, y_test = train_test_split(data.Summary, data['Component/s'], random_state=0, test_size=0.2)
X_train = label_sentences(X_train, 'Train')
X_test = label_sentences(X_test, 'Test')
all_data = X_train + X_test

In [ ]:
model_dbow = Doc2Vec(dm=0, vector_size=300, negative=5, min_count=1, alpha=0.065, min_alpha=0.065)
model_dbow.build_vocab([x for x in tqdm(all_data)])

In [ ]:
for epoch in range(30):
    model_dbow.train(utils.shuffle([x for x in tqdm(all_data)]), total_examples=len(all_data), epochs=1)
    model_dbow.alpha -= 0.002
    model_dbow.min_alpha = model_dbow.alpha

In [ ]:
train_vectors_dbow = get_vectors(model_dbow, len(X_train), 300, 'Train')
test_vectors_dbow = get_vectors(model_dbow, len(X_test), 300, 'Test')

In [ ]:
logreg = LogisticRegression(n_jobs=1, C=1e5)

In [ ]:
logreg = logreg.fit(train_vectors_dbow, y_train)
y_pred = logreg.predict(test_vectors_dbow)

In [ ]:
print('accuracy %s' % accuracy_score(y_pred, y_test))

In [ ]:
Error.err.class_err(y_test,y_pred)

In [ ]:
train_size = int(len(data) * .8)
print ("Train size: %d" % train_size)
print ("Test size: %d" % (len(data) - train_size))

In [ ]:
train_posts = data['Summary'][:train_size]
train_tags = data['Component/s'][:train_size]

test_posts = data['Summary'][train_size:]
test_tags = data['Component/s'][train_size:]

In [ ]:
max_words = 1000
tokenize = text.Tokenizer(num_words=max_words, char_level=False)

In [ ]:
tokenize.fit_on_texts(train_posts) # only fit on train
x_train = tokenize.texts_to_matrix(train_posts)
x_test = tokenize.texts_to_matrix(test_posts)

In [ ]:
encoder = LabelEncoder()
encoder.fit(train_tags)
y_train = encoder.transform(train_tags)
y_test = encoder.transform(test_tags)

In [ ]:
num_classes = np.max(y_train) + 1
y_train = utils.to_categorical(y_train, num_classes)
y_test = utils.to_categorical(y_test, num_classes)

In [ ]:
print('x_train shape:', x_train.shape)
print('x_test shape:', x_test.shape)
print('y_train shape:', y_train.shape)
print('y_test shape:', y_test.shape)

In [ ]:
batch_size = 32
epochs = 5

In [ ]:
model = Sequential()
model.add(Dense(512, input_shape=(max_words,)))
model.add(Activation('relu'))
model.add(Dropout(0.5))
model.add(Dense(num_classes))
model.add(Activation('softmax'))

model.compile(loss='categorical_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])

In [ ]:
history = model.fit(x_train, y_train,
                    batch_size=batch_size,
                    epochs=epochs,
                    verbose=1,
                    validation_split=0.1)

In [ ]:
score = model.evaluate(x_test, y_test,
                       batch_size=batch_size, verbose=1)


In [ ]:
print('Test accuracy:', score[1])

In [ ]:
fig = plt.figure(figsize=(18,6))
data.groupby('Component/s').Summary.count().plot.bar(ylim=0)
plt.ylabel('Count')
plt.title('Number of Issues in each Component')
plt.gcf().subplots_adjust(bottom=0.35)
plt.savefig('Comp.png')
plt.show()

In [ ]:
len(data)

In [ ]:
len(train)

In [ ]:
len(test)